In [1]:
import pandas as pd
import numpy as np
import sys
sys.path.append("/home/missinguser/CSE/single-stage-opt/hybrid_tokamak/laptop/")
import latexplot
latexplot.set_cmap() 

from simsopt import mhd
from simsopt import geo
from simsopt import objectives
import matplotlib.pyplot as plt
from simsopt.mhd.vmec_diagnostics import vmec_compute_geometry
import glob
import py_spec

In [2]:
# delete files that have worse quasisymmetry, leftovers from optimization steps that weren't automatically deleted.
if False:
    directories = {
        "rot_ell (QFB)": "../../freeb_high_aspect_combined",
        "QA_20 (QFB)": "../../freeb_01-01-14-05-28",
        
    }


    def get_qs(surf, res):
        # Vmec setup
        vmec = mhd.Vmec(verbose=False)
        vmec.boundary = surf
        qs = mhd.QuasisymmetryRatioResidual(vmec, surfaces=np.linspace(0.1, 1, 16), helicity_m=1, helicity_n=0, ntheta=32, nphi=32)
        f_qs = qs.total()
        return f_qs

    def dof_from_mpol(mpol):
        return mpol*(mpol*2+1)+mpol 

    # Collect results
    for key, directory in directories.items():
        subdirs = sorted(glob.glob(f"{directory}/mpol*"))
        for subdir in subdirs:
            res = int(subdir.split("mpol")[-1])
            if "freeb" in directory:
                latest_files = sorted(glob.glob(f"{subdir}/*_000_*.end"), key=lambda x: int(x.split("_")[-1].split(".")[0]))
                latest_files = [file.replace(".end", ".h5") for file in latest_files]
                dofs = dof_from_mpol(res)
                qsmin = 1e3
                bestfile = None
                besti = -1
                for i in range(dofs):
                    if i>=len(latest_files):
                        continue
                    latest_file = latest_files[-i-1]
                    if latest_file.endswith(".h5"):
                        spec_output = py_spec.output.SPECout(latest_file)
                        surf = mhd.Spec.pyspec_to_simsopt_surf(spec_output, 0)
                        qs = get_qs(surf, res)
                        if qs < qsmin:
                            qsmin = qs
                            bestfile = latest_file
                            besti=i
                print(bestfile)
                
                
            else:
                # Fixboundary
                pass

In [3]:
# Directories with data
directories = {
    # "QA_20 (QFB)": "../../freeb_12-11-16-48-29",
    "QA_20 (QFB)": "../../freeb_01-02-01-27-47",
    # "QH_10_fr": "../../freeb_12-23-01-03-52", # Needs different QuasisymmetryRatioResidual, since m=1, n=1
    "QA_20 (FI)": "../../fixb_12-31-16-42-24",
    
    # "rot_ell (QFB)": "../../freeb_high_aspect_combined",
    # "rot_ell (FI)": "../../fixb_12-06-11-52-22",
}

import re
import os
def find_matching_h5(directory):
    # Regular expression to match the desired file pattern
    pattern = re.compile(r'.*_000_\d{6}\.sp\.h5$')

    # Get all files in the directory matching the pattern
    matching_files = [os.path.join(directory, f) for f in os.listdir(directory) if pattern.match(f)]
    return matching_files


def find_matching_input(directory):
    # Regular expression to match the desired file pattern
    pattern = re.compile(r'input\..*_000_\d{6}$')

    # Get all files in the directory matching the pattern
    matching_files = [os.path.join(directory, f) for f in os.listdir(directory) if pattern.match(f)]
    return matching_files

def getLgradB(vmec:mhd.Vmec):
    vmec.run()
    s = np.linspace(0.75, 1, 4)
    ntheta = 64
    nphi = 64
    theta = np.linspace(0, 2 * np.pi, ntheta, endpoint=False)
    phi = np.linspace(0, 2 * np.pi / vmec.boundary.nfp, nphi, endpoint=False)
    data = vmec_compute_geometry(vmec, s, theta, phi)
    return np.min(data.L_grad_B)

def get_results(surf, res):
    # Vmec setup
    vmec = mhd.Vmec(verbose=False)
    vmec.boundary = surf
    qs = mhd.QuasisymmetryRatioResidual(vmec, surfaces=np.linspace(0.1, 1, 16), helicity_m=1, helicity_n=0, ntheta=32, nphi=32)
    
    # Compute quantities
    LgradB = getLgradB(vmec)
    mean_iota_diff = (vmec.mean_iota() - 0.4384346834911653) ** 2
    f_qs = qs.total()
    r0_diff = (surf.get_rc(0, 0) - 1.0) ** 2
    A_diff = (surf.aspect_ratio() - 19.595) ** 2
    return {"Directory": key, "Resolution": res, "$f_{QS}$": f_qs, "$(\iota - \iota^*)^2$": mean_iota_diff, "$(R_0 -R_0^*)^2$": r0_diff, "$(A -A^*)^2$": A_diff, "$L^*_{\\nabla B}$":LgradB}

# Collect results
results = []
for key, directory in directories.items():
    subdirs = sorted(glob.glob(f"{directory}/mpol*"))

    if "freeb" in directory:
        # Freeboundary
        first_file = sorted(find_matching_h5(subdirs[0]))[0]
        print(first_file)
        spec_output = py_spec.output.SPECout(first_file)
        surf = mhd.Spec.pyspec_to_simsopt_surf(spec_output, 0)
        results.append(get_results(surf, 0))
    else:
        first_file = sorted(find_matching_input(subdirs[0]))[0] 
        results.append(get_results( geo.SurfaceRZFourier.from_vmec_input(first_file), 0))
    print(first_file)
    for subdir in subdirs:
        res = int(subdir.split("mpol")[-1])
        if "freeb" in directory:
            latest_file = max(find_matching_h5(subdir), key=lambda x: int(x.split("_")[-1].split(".")[0]))
            print(latest_file)
            if latest_file.endswith(".h5"):
                spec_output = py_spec.output.SPECout(latest_file)
                surf = mhd.Spec.pyspec_to_simsopt_surf(spec_output, 0)

                results.append(get_results(surf, res))
        else:
            # Fixboundary
            latest_file = max(find_matching_input(subdir), key=lambda x: int(x.split("_")[-1]))
            print(latest_file)
            results.append(get_results( geo.SurfaceRZFourier.from_vmec_input(latest_file), res))

# Convert to DataFrame
df = pd.DataFrame(results)

# Save as LaTeX table
with open("results_table.tex", "w") as f:
    f.write(df.to_latex(index=False, float_format="%.6f"))



../../freeb_01-02-01-27-47/mpol1/rotating_ellipse_fb_low_000_000000.sp.h5
../../freeb_01-02-01-27-47/mpol1/rotating_ellipse_fb_low_000_000000.sp.h5
../../freeb_01-02-01-27-47/mpol1/rotating_ellipse_fb_low_000_000067.sp.h5
../../freeb_01-02-01-27-47/mpol2/rotating_ellipse_fb_low_000_000222.sp.h5
../../freeb_01-02-01-27-47/mpol3/rotating_ellipse_fb_low_000_000275.sp.h5
../../freeb_01-02-01-27-47/mpol4/rotating_ellipse_fb_low_000_000398.sp.h5
../../freeb_01-02-01-27-47/mpol5/rotating_ellipse_fb_low_000_000591.sp.h5
../../fixb_12-31-16-42-24/mpol1/input.rot_ellipse_000_000000
../../fixb_12-31-16-42-24/mpol1/input.rot_ellipse_000_000051
../../fixb_12-31-16-42-24/mpol2/input.rot_ellipse_000_000192
../../fixb_12-31-16-42-24/mpol3/input.rot_ellipse_000_000456
../../fixb_12-31-16-42-24/mpol4/input.rot_ellipse_000_000948
../../fixb_12-31-16-42-24/mpol5/input.rot_ellipse_000_001330


In [4]:
def dof_from_mpol(mpol):
   return mpol*(mpol*2+1)+mpol 
df["DOFs"] = dof_from_mpol(df["Resolution"])
df.loc[df["Directory"].str.contains("(FI)"), "DOFs"] *= 2
df["DOFs"] = df["DOFs"].astype(int)


/tmp/ipykernel_1317836/3694598775.py:4: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  df.loc[df["Directory"].str.contains("(FI)"), "DOFs"] *= 2


In [5]:

df.loc[df["Directory"].str.contains("(FI)"), "$(R_0 -R_0^*)^2$"] = df.loc[df["Directory"].str.contains("(FI)"), "$(A -A^*)^2$"] 
df["objective $J$"] = df["$(R_0 -R_0^*)^2$"] + df["$(\\iota - \\iota^*)^2$"]*0.1 + df["$f_{QS}$"] 

/tmp/ipykernel_1317836/588836030.py:1: UserWarning: This pattern is interpreted as a regular expression, and has match groups. To actually get the groups, use str.extract.
  df.loc[df["Directory"].str.contains("(FI)"), "$(R_0 -R_0^*)^2$"] = df.loc[df["Directory"].str.contains("(FI)"), "$(A -A^*)^2$"]


In [6]:
latexplot.set_cmap(len(df["Directory"].unique()))
fig = latexplot.figure()
import matplotlib.pyplot as plt
from matplotlib.gridspec import GridSpec

# Plotting f_{QS} vs Resolution
xval = "DOFs"
plot_keys = ["objective $J$", "$f_{QS}$", "$(\iota - \iota^*)^2$", "$(R_0 -R_0^*)^2$"]

# Create a figure and define GridSpec layout
gs = GridSpec(3, 2, width_ratios=[3, 1], wspace=0.3)  # Larger width for the objective plot

# Plot the large objective function subplot
ax1 = fig.add_subplot(gs[:,0])
for directory in df["Directory"].unique():
    subdf = df[df["Directory"] == directory].sort_values(by=xval)
    ax1.semilogy(subdf[xval], subdf[plot_keys[0]], label=directory, marker="o")
ax1.set_xlabel(xval)
ax1.set_ylabel(plot_keys[0])
ax1.legend()
ax1.set_title("Objective Function")

# Create a column of three smaller subplots
for i, key in enumerate(plot_keys[1:]):
    ax = fig.add_subplot(gs[i,1])  # Adjust position for each subplot
    for directory in df["Directory"].unique():
        subdf = df[df["Directory"] == directory].sort_values(by=xval)
        ax.semilogy(subdf[xval], subdf[key], label=directory, marker="o")
    ax.set_xlabel(xval)
    ax.set_ylabel(key)

    if i == 2:
        ax2 = ax.twinx()  # instantiate a second Axes that shares the same x-axis
        subdf = df[df["Directory"] == directory].sort_values(by=xval)
        for directory in df["Directory"].unique():
            subdf = df[df["Directory"] == directory].sort_values(by=xval)
            ax2.semilogy(subdf[xval], subdf[key], label=directory, marker="o")
        ax2.set_xlabel(xval)
        key = "$(A -A^*)^2$"
        ax2.set_ylabel(key)



# Save and show the plot
latexplot.savenshow("f_qs_vs_resolution")


/home/missinguser/CSE/single-stage-opt/hybrid_tokamak/laptop/latexplot.py:87: UserWarning: This figure includes Axes that are not compatible with tight_layout, so results might be incorrect.
  plt.tight_layout()
/home/missinguser/CSE/single-stage-opt/hybrid_tokamak/laptop/latexplot.py:91: UserWarning: FigureCanvasPgf is non-interactive, and thus cannot be shown
  plt.show()


In [7]:
# Save as LaTeX table
with open("results_table.tex", "w") as f:
    f.write(df.rename({
        "Directory": "Optimization run",
    }, axis=1).to_latex(index=False, float_format="%.6f"))

In [8]:
df.rename({
        "Directory": "Optimization run",
}, axis=1)

Optimization run  Resolution  $f_{QS}$  $(\iota - \iota^*)^2$  \
0       QA_20 (QFB)           0  0.039830           4.213691e-03   
1       QA_20 (QFB)           1  0.007694           2.795533e-07   
2       QA_20 (QFB)           2  0.005627           6.531284e-03   
3       QA_20 (QFB)           3  0.000387           1.467653e-04   
4       QA_20 (QFB)           4  0.000205           9.726673e-05   
5       QA_20 (QFB)           5  0.000202           3.519597e-05   
6        QA_20 (FI)           0  0.039881           4.330685e-03   
7        QA_20 (FI)           1  0.007989           3.310351e-04   
8        QA_20 (FI)           2  0.000165           2.536747e-06   
9        QA_20 (FI)           3  0.000051           4.334293e-06   
10       QA_20 (FI)           4  0.000033           4.626527e-07   
11       QA_20 (FI)           5  0.000026           1.110168e-07   

    $(R_0 -R_0^*)^2$  $(A -A^*)^2$  $L^*_{\nabla B}$  DOFs  objective $J$  
0       1.413455e-06  3.158180e-02          0.475654     0       0.040253  
1       1.814392e-03  1.003642e-01          0.456475     4       0.009508  
2       1.040144e-05  4.062045e-02          0.501929    12       0.006291  
3       2.905608e-05  6.014708e-02          0.368010    24       0.000430  
4       8.882521e-06  4.938977e-02          0.317383    40       0.000223  
5       6.314409e-06  4.714308e-02          0.343886    60       0.000212  
6       3.153559e-02  3.153559e-02          0.480553     0       0.071849  
7       2.671019e-02  2.671019e-02          0.439916     8       0.034732  
8       6.222950e-07  6.222950e-07          0.275901    24       0.000166  
9       6.349493e-07  6.349493e-07          0.331958    48       0.000052  
10      6.142312e-07  6.142312e-07          0.351300    80       0.000034  
11      6.159390e-07  6.159390e-07          0.344094   120       0.000027

In [9]:
fig, axs = plt.subplots(1,2, sharey=True, figsize=latexplot.get_size(1))
plt.sca(axs[0])
xval= "DOFs"
yval = "$L^*_{\\nabla B}$"
for directory in df["Directory"].unique():
    subdf = df[df["Directory"] == directory].sort_values(by=xval)
    plt.semilogy(subdf[xval], subdf[yval], label=directory, marker="o")
plt.legend()
plt.xlabel(xval)
plt.ylabel(yval)

plt.sca(axs[1])
xval = "$f_{QS}$"
for directory in df["Directory"].unique():
    subdf = df[df["Directory"] == directory].sort_values(by=xval)
    plt.loglog(subdf[xval], subdf[yval], label=directory, marker="o")
plt.legend()
plt.xlabel(xval)
plt.ylabel(yval)

latexplot.savenshow("lgradb_vs_resolution")

/home/missinguser/CSE/single-stage-opt/hybrid_tokamak/laptop/latexplot.py:91: UserWarning: FigureCanvasPgf is non-interactive, and thus cannot be shown
  plt.show()


# Filamment coil complexity

In [18]:
import os
import matplotlib.pyplot as plt
from pathlib import Path
import numpy as np
from scipy.optimize import minimize
from simsopt.field import BiotSavart, Current, coils_via_symmetries
from simsopt.geo import (SurfaceRZFourier, curves_to_vtk, create_equally_spaced_curves,
                         CurveLength, CurveCurveDistance, MeanSquaredCurvature,
                         LpCurveCurvature, CurveSurfaceDistance)
from simsopt.objectives import Weight, SquaredFlux, QuadraticPenalty

# Number of unique coil shapes, i.e. the number of coils per half field period:
# (Since the configuration has nfp = 2, multiply by 4 to get the total number of coils.)
ncoils = 3

# Major radius for the initial circular coils:
R0 = 1.0

# Minor radius for the initial circular coils:
R1 = 0.5

# Number of Fourier modes describing each Cartesian component of each coil:
order = 5

# Threshold and weight for the coil-to-coil distance penalty in the objective function:
CC_THRESHOLD = 0.05
CC_WEIGHT = 1

# Threshold and weight for the coil-to-surface distance penalty in the objective function:
CS_THRESHOLD = 0.12
CS_WEIGHT = 1

# Threshold and weight for the curvature penalty in the objective function:
CURVATURE_THRESHOLD = 10
CURVATURE_WEIGHT = 1e-6

# Threshold and weight for the mean squared curvature penalty in the objective function:
MSC_THRESHOLD = 10
MSC_WEIGHT = 1e-6


# Number of iterations to perform:
MAXITER = 150

# Directory for output
OUT_DIR = "./output/"
os.makedirs(OUT_DIR, exist_ok=True)

In [19]:
def optimize(s:SurfaceRZFourier):
    LENGTH_WEIGHT = Weight(1e-5)
    # Weight on the curve lengths in the objective function. We use the `Weight`
    # class here to later easily adjust the scalar value and rerun the optimization
    # without having to rebuild the objective.
    # Initialize the boundary magnetic surface:

    s = s.copy(
        nphi = 64,
        ntheta = 64,
        # range="half period"
        range="field period"
    )

    # Create the initial coils:
    base_curves = create_equally_spaced_curves(ncoils, s.nfp, stellsym=False, R0=R0, R1=R1, order=order)
    base_currents = [Current(1e5) for i in range(ncoils)]
    # Since the target field is zero, one possible solution is just to set all
    # currents to 0. To avoid the minimizer finding that solution, we fix one
    # of the currents:
    base_currents[0].fix_all()

    coils = coils_via_symmetries(base_curves, base_currents, s.nfp, False)
    bs = BiotSavart(coils)
    bs.set_points(s.gamma().reshape((-1, 3)))

    curves = [c.curve for c in coils]
    
    # Define the individual terms objective function:
    Jf = SquaredFlux(s, bs)
    Jls = [CurveLength(c) for c in base_curves]
    Jccdist = CurveCurveDistance(curves, CC_THRESHOLD, num_basecurves=ncoils)
    Jcsdist = CurveSurfaceDistance(curves, s, CS_THRESHOLD)
    Jcs = [LpCurveCurvature(c, 2, CURVATURE_THRESHOLD) for c in base_curves]
    Jmscs = [MeanSquaredCurvature(c) for c in base_curves]


    # Form the total objective function. To do this, we can exploit the
    # fact that Optimizable objects with J() and dJ() functions can be
    # multiplied by scalars and added:
    JF = Jf \
        + LENGTH_WEIGHT * sum(Jls) \
        + CS_WEIGHT * Jcsdist \
        + CC_WEIGHT * Jccdist \
        + CURVATURE_WEIGHT * sum(Jcs) \
        # + MSC_WEIGHT * sum(QuadraticPenalty(J, MSC_THRESHOLD, "max") for J in Jmscs)

    # We don't have a general interface in SIMSOPT for optimisation problems that
    # are not in least-squares form, so we write a little wrapper function that we
    # pass directly to scipy.optimize.minimize


    def fun(dofs):
        JF.x = dofs
        J = JF.J()
        grad = JF.dJ()
        # jf = Jf.J()
        # BdotN = np.mean(np.abs(np.sum(bs.B().reshape(s.unitnormal().shape) * s.unitnormal(), axis=2)))
        return J, grad

    dofs = JF.x
    
    print("### Run the optimisation #####################################################")
    res = minimize(fun, dofs, jac=True, method='L-BFGS-B', options={'maxiter': MAXITER}, tol=1e-12)


    # We now use the result from the optimization as the initial guess for a
    # subsequent optimization with reduced penalty for the coil length. This will
    # result in slightly longer coils but smaller `B·n` on the surface.
    dofs = res.x
    LENGTH_WEIGHT *= 0.1
    res = minimize(fun, dofs, jac=True, method='L-BFGS-B', options={'maxiter': MAXITER}, tol=1e-15)


    # Define the individual terms objective function:
    Jf = SquaredFlux(s, bs)
    Jls = [CurveLength(c) for c in base_curves]
    Jccdist = CurveCurveDistance(curves, 0, num_basecurves=ncoils)
    Jcsdist = CurveSurfaceDistance(curves, s, R0)
    Jcs = [LpCurveCurvature(c, 2, CURVATURE_THRESHOLD) for c in base_curves]
    Jmscs = [MeanSquaredCurvature(c) for c in base_curves]

    gammas = surf.gamma().reshape((-1, 3))
    def coildist(gammac):
        dists = np.sqrt(np.sum(
            (gammac[:, None, :] - gammas[None, :, :])**2, axis=2))
        return dists
    return coils, float(JF.J()), Jf.J(), np.min([np.min(coildist(c.gamma().reshape((-1, 3)))) for c in curves])


In [20]:
coil_res = []
for key, directory in directories.items():
    subdirs = sorted(glob.glob(f"{directory}/mpol*"))
    # subdirs = subdirs[-1:]

    if "freeb" in directory:
        # Freeboundary
        first_file = sorted(find_matching_h5(subdirs[0]))[0]
        print(first_file)
        spec_output = py_spec.output.SPECout(first_file)
        surf = mhd.Spec.pyspec_to_simsopt_surf(spec_output, 0)
        coil_res.append(optimize(surf))
    else:
        first_file = sorted(find_matching_input(subdirs[0]))[0] 
        coil_res.append(optimize( geo.SurfaceRZFourier.from_vmec_input(first_file)))
    print(first_file)
    for subdir in subdirs:
        res = int(subdir.split("mpol")[1])
        if "freeb" in directory:
            latest_file = max(find_matching_h5(subdir), key=lambda x: int(x.split("_")[-1].split(".")[0]))
            print(latest_file)
            if latest_file.endswith(".h5"):
                spec_output = py_spec.output.SPECout(latest_file)
                surf = mhd.Spec.pyspec_to_simsopt_surf(spec_output, 0)

                coil_res.append(optimize(surf))
        else:
            # Fixboundary
            latest_file = max(find_matching_input(subdir), key=lambda x: int(x.split("_")[-1]))
            print(latest_file)
            surf = geo.SurfaceRZFourier.from_vmec_input(latest_file)
            coil_res.append(optimize( surf))

        geo.plot([surf]+coil_res[-1][0], engine="plotly", close=True, show=True)
print("done")


../../freeb_01-02-01-27-47/mpol1/rotating_ellipse_fb_low_000_000000.sp.h5
### Run the optimisation #####################################################
../../freeb_01-02-01-27-47/mpol1/rotating_ellipse_fb_low_000_000000.sp.h5
../../freeb_01-02-01-27-47/mpol1/rotating_ellipse_fb_low_000_000067.sp.h5
### Run the optimisation #####################################################


../../freeb_01-02-01-27-47/mpol2/rotating_ellipse_fb_low_000_000222.sp.h5
### Run the optimisation #####################################################


../../freeb_01-02-01-27-47/mpol3/rotating_ellipse_fb_low_000_000275.sp.h5
### Run the optimisation #####################################################


../../freeb_01-02-01-27-47/mpol4/rotating_ellipse_fb_low_000_000398.sp.h5
### Run the optimisation #####################################################


../../freeb_01-02-01-27-47/mpol5/rotating_ellipse_fb_low_000_000591.sp.h5
### Run the optimisation #####################################################


...

../../fixb_12-31-16-42-24/mpol2/input.rot_ellipse_000_000192
### Run the optimisation #####################################################


../../fixb_12-31-16-42-24/mpol3/input.rot_ellipse_000_000456
### Run the optimisation #####################################################


../../fixb_12-31-16-42-24/mpol4/input.rot_ellipse_000_000948
### Run the optimisation #####################################################


../../fixb_12-31-16-42-24/mpol5/input.rot_ellipse_000_001330
### Run the optimisation #####################################################


done


In [13]:
[r[1:] for r in coil_res]

[(1.1049208538005087e-05, 5.785584130049418e-07, 0.22857521788327764),
 (1.0575874088644094e-05, 5.55677324746182e-07, 0.20938925733462105),
 (9.99517509864911e-06, 6.305343630791461e-07, 0.23367818464861898),
 (1.2636576062366781e-05, 1.562661695552902e-06, 0.1633114678383701),
 (1.2832998124452503e-05, 1.9193354287584076e-06, 0.15317586703905986),
 (1.2754342015680908e-05, 1.8264391113093624e-06, 0.15325212754874828),
 (1.1049016366856304e-05, 5.878871905370708e-07, 0.24441761418093566),
 (1.1281744417482715e-05, 1.1137513733880272e-06, 0.22374597750550962),
 (1.460652016586681e-05, 3.8077952007706972e-06, 0.15021050547160678),
 (1.3870052367977746e-05, 2.9428052417882343e-06, 0.1466478032586457),
 (1.3745322837034894e-05, 2.7892550769541367e-06, 0.14659586658426343),
 (1.5046975784692374e-05, 2.753202406814879e-06, 0.14825772658718853)]

In [14]:
assert coil_res[0][3] > coil_res[1][3], f"{coil_res[0][3]} < {coil_res[1][3]}"

In [15]:
assert coil_res[0][1] < coil_res[1][1], f"{coil_res[0][1]} >= {coil_res[1][1]}"

AssertionError: 1.1049208538005087e-05 >= 1.0575874088644094e-05

In [ ]:
def poincare_for_coils(coils):
    from simsopt import field
    nfieldlines = 32
    rr = np.linspace(R0, R0+R1/2, nfieldlines)
    Z0 = np.zeros(nfieldlines)

    n = 64
    degree = 3
    rrange = (R0, R0+R1/5, n) 
    phirange = (0, 2*np.pi/surf.nfp, 4*n*2)
    # exploit stellarator symmetry and only consider positive z values:
    zrange = (0, R1/5, n//2)
    bs = BiotSavart(coils)
    # bs.set_points_cart(np.array([[0,R0, 0], [0,R0, 0.1]]))
    # print(bs.B())  
    bsh = field.InterpolatedField(
        bs, degree, rrange, phirange, zrange, True, nfp=surf.nfp, stellsym=False
    )

    bsh.set_points(surf.gamma().reshape((-1, 3)))
    bs.set_points(surf.gamma().reshape((-1, 3)))
    Bh = bsh.B()
    B = bs.B()
    print("Mean(|B|) on plasma surface =", np.mean(bs.AbsB()))
    print("|B-Bh| on surface:", np.sort(np.abs(B-Bh).flatten()))
    from simsopt import util
    util.make_Bnormal_plots(bsh, surf, "fieldlines", "Binterpolated_pre_poincare_check")

    print("Constructed fieldline interpolant")
    phis = [(i/4)*(2*np.pi/surf.nfp) for i in range(4)]
    fieldlines_tys, fieldlines_phi_hits = field.compute_fieldlines(
        bsh, rr, Z0, tol=1e-14, tmax=40000,
        phis=phis, stopping_criteria=[
            field.MinRStoppingCriterion(R0-R1/2),
            field.MaxRStoppingCriterion(R0+R1/2), 
            field.IterationStoppingCriterion(200000),
                                    ])
    print(f"Time for fieldline. Num steps={sum([len(l) for l in fieldlines_tys])//nfieldlines}", flush=True)
    field.plot_poincare_data(fieldlines_phi_hits, phis, f'poincare_fieldline_.png', dpi=650) 

poincare_for_coils(coil_res[-1][0])

Mean(|B|) on plasma surface = 0.4993667742178944
|B-Bh| on surface: [1.43470305e-14 2.55742489e-14 3.13360449e-14 ... 5.18200346e-01
 5.18230682e-01 5.18238394e-01]
Constructed fieldline interpolant
Time for fieldline. Num steps=1013


In [ ]:
from simsopt import util, field
# util.run_Poincare_plots(surf, BiotSavart(coil_res[1][0]), field.DipoleField() filename_poincare="poincare_fieldline.png")
util.trace_fieldlines(BiotSavart(coil_res[-1][0]), "s=1",  surf, None, "fieldlines")

In [ ]:
util.calculate_on_axis_B(BiotSavart(coil_res[-1][0]), surf)
util.make_Bnormal_plots(BiotSavart(coil_res[-1][0]), surf, "fieldlines", "biot_savart_pre_poincare_check")

Bmag at R =  0.998806980557671 , Z = 0:  [0.30441541 0.3048963  0.30331039 0.30044388 0.29816065 0.29751604
 0.29772737 0.2979008  0.29857859 0.30045987 0.30289897 0.30473012
 0.30445965 0.30490118 0.30382303 0.3009563  0.29849328 0.29756268
 0.29766024 0.29786324 0.29838449 0.29994868 0.30238648 0.30457439
 0.30458142 0.30479055 0.30422732 0.30149725 0.29891996 0.29764286
 0.29759081 0.29784096 0.29821594 0.29948682 0.30191443 0.30431398
 0.30471701 0.3046226  0.30453773 0.30208852 0.29941303 0.29775803
 0.29753467 0.29781753 0.29807479 0.29910686 0.30145534 0.30392666
 0.30480201 0.30447671 0.30476654 0.30271214 0.29993068 0.29792245
 0.29750681 0.29778109 0.29796883 0.2988111  0.30097272 0.30343345
 0.30480572]
toroidally averaged Bmag at R =  0.998806980557671 , Z = 0:  0.30098389069053305


In [ ]:
df["$L_{filament}$"] = [r[-1] for r in coil_res] 
df["$\\chi_B$"] = [r[3] for r in coil_res] 

In [ ]:
df.iloc[0] = df.iloc[6]
df.loc[0, "Directory"] = "QA_20 (QFB)" 
df

Directory  Resolution  $f_{QS}$  $(\iota - \iota^*)^2$  \
0   QA_20 (QFB)         0.0  0.039881           4.330685e-03   
1   QA_20 (QFB)         1.0  0.007694           2.795533e-07   
2   QA_20 (QFB)         2.0  0.005627           6.531284e-03   
3   QA_20 (QFB)         3.0  0.000387           1.467653e-04   
4   QA_20 (QFB)         4.0  0.000205           9.726673e-05   
5   QA_20 (QFB)         5.0  0.000202           3.519597e-05   
6    QA_20 (FI)         0.0  0.039881           4.330685e-03   
7    QA_20 (FI)         1.0  0.007989           3.310351e-04   
8    QA_20 (FI)         2.0  0.000165           2.536747e-06   
9    QA_20 (FI)         3.0  0.000051           4.334293e-06   
10   QA_20 (FI)         4.0  0.000033           4.626527e-07   
11   QA_20 (FI)         5.0  0.000026           1.110168e-07   

    $(R_0 -R_0^*)^2$  $(A -A^*)^2$  $L^*_{\nabla B}$   DOFs  objective $J$  \
0       3.153559e-02  3.153559e-02          0.480553    0.0       0.071849   
1       1.814392e-03  1.003642e-01          0.456475    4.0       0.009508   
2       1.040144e-05  4.062045e-02          0.501929   12.0       0.006291   
3       2.905608e-05  6.014708e-02          0.368010   24.0       0.000430   
4       8.882521e-06  4.938977e-02          0.317383   40.0       0.000223   
5       6.314409e-06  4.714308e-02          0.343886   60.0       0.000212   
6       3.153559e-02  3.153559e-02          0.480553    0.0       0.071849   
7       2.671019e-02  2.671019e-02          0.439916    8.0       0.034732   
8       6.222950e-07  6.222950e-07          0.275901   24.0       0.000166   
9       6.349493e-07  6.349493e-07          0.331958   48.0       0.000052   
10      6.142312e-07  6.142312e-07          0.351300   80.0       0.000034   
11      6.159390e-07  6.159390e-07          0.344094  120.0       0.000027   

    $L_{filament}$  $\chi_B$  
0         0.243431  0.243431  
1         0.207490  0.207490  
2         0.233860  0.233860  
3         0.162931  0.162931  
4         0.153176  0.153176  
5         0.153629  0.153629  
6         0.243431  0.243431  
7         0.226417  0.226417  
8         0.150202  0.150202  
9         0.146864  0.146864  
10        0.146422  0.146422  
11        0.148398  0.148398

In [ ]:
for yval in ["$L_{filament}$", "$L^*_{\\nabla B}$"]:
    fig, axs = plt.subplots(1,2, sharey=True, figsize=latexplot.get_size(1))
    plt.sca(axs[0])
    xval= "DOFs"
    for directory in df["Directory"].unique():
        subdf = df[df["Directory"] == directory].sort_values(by=xval)
        plt.semilogy(subdf[xval], subdf[yval], label=directory, marker="o")
    plt.legend()
    plt.xlabel(xval)
    plt.ylabel(yval)

    plt.sca(axs[1])
    xval = "$f_{QS}$"
    for directory in df["Directory"].unique():
        subdf = df[df["Directory"] == directory].sort_values(by=xval)
        plt.loglog(subdf[xval], subdf[yval], label=directory, marker="o")
    plt.legend()
    plt.gca().invert_xaxis()
    plt.xlabel(xval)
    plt.ylabel(yval)

    name = re.sub('\W+','', yval ).lower()+"_vs_resolution"
    latexplot.savenshow(name)

/home/missinguser/CSE/single-stage-opt/hybrid_tokamak/laptop/latexplot.py:90: UserWarning:

FigureCanvasPgf is non-interactive, and thus cannot be shown

/home/missinguser/CSE/single-stage-opt/hybrid_tokamak/laptop/latexplot.py:90: UserWarning:

FigureCanvasPgf is non-interactive, and thus cannot be shown

